In [6]:
pip uninstall tensorflow


Found existing installation: tensorflow 2.18.0
Uninstalling tensorflow-2.18.0:
  Would remove:
    /Users/mcbookairdebat/Library/Python/3.9/bin/import_pb_to_tensorboard
    /Users/mcbookairdebat/Library/Python/3.9/bin/saved_model_cli
    /Users/mcbookairdebat/Library/Python/3.9/bin/tensorboard
    /Users/mcbookairdebat/Library/Python/3.9/bin/tf_upgrade_v2
    /Users/mcbookairdebat/Library/Python/3.9/bin/tflite_convert
    /Users/mcbookairdebat/Library/Python/3.9/bin/toco
    /Users/mcbookairdebat/Library/Python/3.9/bin/toco_from_protos
    /Users/mcbookairdebat/Library/Python/3.9/lib/python/site-packages/tensorflow-2.18.0.dist-info/*
    /Users/mcbookairdebat/Library/Python/3.9/lib/python/site-packages/tensorflow/*
  Would not remove (might be manually added):
    /Users/mcbookairdebat/Library/Python/3.9/lib/python/site-packages/tensorflow/compiler/mlir/quantization/tensorflow/calibrator/pywrap_calibration.pyi
    /Users/mcbookairdebat/Library/Python/3.9/lib/python/site-packages/tensor

In [7]:
import numpy as np 
from scipy.stats import norm
from math import log, sqrt, exp
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers
from tensorflow.keras.optimizers import Adam
import tensorflow_probability as tfp
import pandas as pd
import os
os.chdir("/Users/mcbookairdebat/Desktop/Projet/project/GitHub/Deep_hedging_research/Deep_Hedging/Deep_hedging_Hull")
from utils import *


ImportError: cannot import name 'keras' from 'tensorflow' (unknown location)

In [4]:

# ------------------------------
# Parameters for the simulation
# ------------------------------
S0 = 100.0      # initial underlying price
K  = 100.0      # strike
r  = 0.02       # annual risk-free rate
sigma = 0.20    # volatility (20%)
T  = 1.0        # maturity in years (1 year)
steps = 20     # number of discrete hedging steps
dt = T / steps  # length of each time step
nb_simul = 100000
costs = [0.0,0.001,0.002,0.005]



In [10]:
path,option_price_path, delta_path = get_sim_path(M=steps, freq=1, num_sim=10000)

1. generate asset price paths
2. generate BS price and delta
simulation done!


/Users/mcbookairdebat/Desktop/Projet/project/GitHub/Deep_hedging_research/Deep_Hedging/Deep_hedging_Hull/utils.py:87: RuntimeWarning:

divide by zero encountered in divide



NameError: name 'tfp' is not defined

In [29]:
def compute_rewards(
    path: np.ndarray,
    option_price_path: np.ndarray,
    delta_path: np.ndarray,
    strike_price: float,
    spread: float,
):

    N, total_T = path.shape
    T = total_T - 1 
    
    # Prepare an array to store the rewards: shape (N, T)
    rewards = np.zeros((N, T), dtype=np.float64)
    
    # Loop over each path
    for i in range(N):
        # For each time step t from 0 to T-1
        for t in range(T):
            current_price = path[i, t]
            current_option_price = option_price_path[i, t]
            current_position = delta_path[i, t]

            next_price = path[i, t+1]
            next_option_price = option_price_path[i, t+1]
            next_position = delta_path[i, t+1]

            # ---------------------
            # Reward calculation
            # ---------------------
            # 1) PnL from underlying movement:
            #    (next_price - current_price) * next_position / 100
            # 2) Minus transaction costs from changing the hedge position:
            #    |current_position - next_position| * current_price * (spread / 100)
            reward_t = (next_price - current_price) * next_position \
                       - abs(current_position - next_position) * current_price * spread

            # Final step adjustments:
            if t == T - 1:
                payoff_diff = (max(next_price - strike_price, 0.0) - next_option_price)
                cost_to_close = next_position * next_price * spread
                reward_t -= payoff_diff + cost_to_close
            else:

                reward_t -= (next_option_price - current_option_price)

            rewards[i, t] = reward_t

    return rewards


In [30]:
rewards = compute_rewards(path,option_price_path, delta_path,strike_price=100,spread=0.0)


In [ ]:
rewards = pd.DataFrame(rewards)
rewards = rewards.T 
fig = go.Figure()
# Add traces for each column
for column in rewards.columns:
    fig.add_trace(go.Scatter(x=rewards.index, y=rewards[column], mode='lines', name=f"action{column}"))
    #fig.add_trace(go.Scatter(x=deltas.index, y=deltas[column], mode='lines', name=f"deltas{column}"))

# Update layout
fig.update_layout(
    title='Evolution of Delta Black and scholes and from the model',
    xaxis_title='Time to matuirity',
    yaxis_title='Delta',
    template='plotly',
    legend=dict(title='Columns'),
)

# Show the plot
fig.show()


In [21]:
fig = px.histogram(rewards.iloc[19])
fig.show()

# Make the plot for delta for different time to maturity and different stike 

# try to construct a small neural network that takes time to matuirity and moneyness and get the delta 

In [51]:
moneyness_path = K/path

In [53]:
moneyness_path = moneyness_path.T


In [55]:
moneyness_path

array([[1.        , 1.01242288, 1.00316177, ..., 0.9953907 , 0.96850559,
        0.96543139],
       [1.        , 1.01987066, 1.01429106, ..., 0.97028474, 0.95574677,
        0.9745408 ],
       [1.        , 0.999832  , 1.0031775 , ..., 1.0342794 , 1.04558037,
        1.0435978 ],
       ...,
       [1.        , 1.00602122, 0.99677147, ..., 1.05002004, 1.05977693,
        1.07797237],
       [1.        , 0.98937416, 0.98095352, ..., 0.92555348, 0.91920293,
        0.91424575],
       [1.        , 0.99982781, 1.02942825, ..., 0.97481811, 0.96889603,
        0.98480105]])

# Buil a neural network to predict y 

In [62]:

model = keras.Sequential([
    layers.Dense(32,input_shape=(21,)),  
    layers.BatchNormalization(),                         
    layers.Activation('relu'),
    layers.Dropout(0.2),

    layers.Dense(64, use_bias=False),
    layers.BatchNormalization(),
    layers.Activation('relu'),
    layers.Dropout(0.2),

    layers.Dense(32, use_bias=False),
    layers.BatchNormalization(),
    layers.Activation('relu'),
    layers.Dropout(0.2),

    layers.Dense(20, use_bias=False),
    layers.Activation('relu'),
    # Output layer with 1 neuron (sigmoid -> output in [0, 1])
    layers.Dense(1, activation='linear')
])

def custom_loss(y_true, y_pred):
    # Example: Mean Squared Error with an additional penalty
    mse = tf.reduce_mean(tf.square(y_pred- y_true))

     # Add a penalty term
    return mse + 0.01* tf.sqrt((tf.reduce_mean(tf.square(y_pred)) - tf.square(tf.reduce_mean(y_pred))))
def custom_loss2(y_true, y_pred):
    # Example: Mean Squared Error with an additional penalty
    alpha = 0.05
    VaR = np.quantile(y_pred,q=alpha)

    ES_alpha = tf.reduce_mean(y_pred[tf.where(y_pred<VaR)])

     # Add a penalty term
    return ES_alpha


# 3. Compile the model
model.compile(optimizer=Adam(learning_rate=0.001),
              loss=custom_loss2,
              metrics=['accuracy'])

# 4. Train the model
history = model.fit(
    moneyness_path, rewards,
    epochs=5,
    batch_size=128,
    validation_split=0.1,  # 20% of data for validation
    verbose=1
)


Epoch 1/5


NotImplementedError: Cannot convert a symbolic tf.Tensor (sequential_6_1/dense_34_1/Add:0) to a numpy array. This error may indicate that you're trying to pass a Tensor to a NumPy call, which is not supported.

In [15]:
tf.keras.utils.plot_model(UNet,show_shapes=True)
# 5. Evaluate on the entire dataset
loss, accuracy = model.evaluate(X_test, Y_test, verbose=0)
print(f"Final Training Loss: {loss:.4f}")
print(f"Final Training Accuracy: {accuracy:.4f}")


Final Training Loss: 0.0032
Final Training Accuracy: 0.0464


In [16]:
X_test

array([[17.        ,  0.98321265],
       [18.        ,  0.95170985],
       [19.        ,  0.96956387],
       ...,
       [18.        ,  0.88575113],
       [19.        ,  0.88991282],
       [20.        ,  0.87653509]])

In [17]:
moneyness = np.linspace(0, 2.5, 1000)
time_to_maturity = np.linspace(0, 20, 21)[::-1]
Moneyness,Time = np.meshgrid(moneyness,time_to_maturity)
data= {
    'Time to Maturity': Time.ravel(),'Moneyness': Moneyness.ravel()
    
}
df = pd.DataFrame(data)
S_test = K/Moneyness
option_type ='call'
def vectorized_delta(option_type, S, K, T, r, sigma):
    """
    Vectorized Delta calculation for arrays of S and T.
    """
    # Avoid division by zero
    T = np.where(T <= 0, 1e-6, T)
    d1 = (np.log(S / K) + (r + 0.5 * sigma ** 2) * T) / (sigma * np.sqrt(T))
    

    delta = norm.cdf(d1)
   
    
    return delta
Delta = vectorized_delta('call', S_test, K, Time, r, sigma)
df['Delta_bs'] = Delta.flatten()

fig = go.Figure(data=[go.Surface(
    x=Moneyness,
    y=Time,
    z=Delta,
    colorscale='Viridis',
    colorbar=dict(title='Delta'),
    contours = {
        "x": {"show": True, "start":0.5, "end":1.5, "size":0.1},
        "y": {"show": True, "start":0.0, "end":2.0, "size":0.2},
        "z": {"show": True, "size":0.05}
    }
)])

# Update layout for better aesthetics
fig.update_layout(
    title=f'Option Delta Surface ({option_type.capitalize()})',
    scene=dict(
        xaxis_title='Moneyness (S/K)',
        yaxis_title='Time to Maturity (Years)',
        zaxis_title='Delta',
        xaxis=dict(nticks=10, range=[0.25, 2.5]),
        yaxis=dict(nticks=10, range=[0, 20]),
        zaxis=dict(nticks=10, range=[0, 1] if option_type == 'call' else [-1, 0]),
    ),
    width=800,
    height=700,
    autosize=False
)

# Add interactive hover information
fig.update_traces(
    hovertemplate='Moneyness: %{x:.2f}<br>Time: %{y:.2f} yr<br>Delta: %{z:.2f}<extra></extra>'
)

# Show the figure
fig.show()

/var/folders/lc/t3q2r39x05ndfqz7hm78wmkc0000gn/T/ipykernel_50953/2362768988.py:9: RuntimeWarning:

divide by zero encountered in divide



In [18]:
df['Delta'] = model.predict(np.array(df.iloc[:,:2]))

657/657 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step


In [19]:
df['Calibrage_BS'] = df.Delta_bs - df.Delta

In [20]:
df

Time to Maturity  Moneyness  Delta_bs     Delta  Calibrage_BS
0                  20.0   0.000000       1.0  0.999782      0.000218
1                  20.0   0.002503       1.0  0.999779      0.000221
2                  20.0   0.005005       1.0  0.999775      0.000225
3                  20.0   0.007508       1.0  0.999771      0.000229
4                  20.0   0.010010       1.0  0.999767      0.000233
...                 ...        ...       ...       ...           ...
20995               0.0   2.489990       0.0  0.445545     -0.445545
20996               0.0   2.492492       0.0  0.444933     -0.444933
20997               0.0   2.494995       0.0  0.444321     -0.444321
20998               0.0   2.497497       0.0  0.443709     -0.443709
20999               0.0   2.500000       0.0  0.443098     -0.443098

[21000 rows x 5 columns]

In [21]:
import numpy as np
import plotly.graph_objects as go

# Assuming your DataFrame is named df
# Extract the columns
time_to_maturity = np.array(df['Time to Maturity'])
moneyness = np.array(df['Moneyness'])
delta = np.array(df['Calibrage_BS']).reshape(21,1000)


In [22]:

# Create an interactive 3D surface plot
fig = go.Figure(data=[go.Surface(
    z=delta,x=Moneyness,
    y=Time,
    colorscale= 'twilight', colorbar=dict(title='Delta')
)])

# Add layout details
fig.update_layout(
    title=f'Option Delta Surface ({option_type.capitalize()})',
    scene=dict(
        xaxis_title='Moneyness (S/K)',
        yaxis_title='Time to Maturity (Years)',
        zaxis_title='Delta_difference',
        xaxis=dict(nticks=10, range=[0.25, 2.5]),
        yaxis=dict(nticks=10, range=[0, 20]),
        zaxis=dict(nticks=10, range=[-1, 1] if option_type == 'call' else [-1, 0]),
    ),
    width=800,
    height=700,
    autosize=False
)


# Show the plot
fig.show()



Try to train a model on a total path and train the model to be not to far that the full delta but also to maximise the reward coming from the delta hedging 

## 1. Dataset 

In [23]:
S = simulation_path(S0,K,r,sigma,steps,nb_simul)/K
ttm = list(np.linspace(0,20,21,dtype ='int'))[::-1]*nb_simul

In [24]:
dataset = pd.DataFrame(S.T.flatten(),columns=['S'])
dataset['ttm'] = ttm

In [25]:
dataset.iloc[1,0]

1.0680775674046006

In [26]:
dataset['delta'] = [bs_call_delta(dataset.iloc[i,0]*K,K,r,sigma,dataset.iloc[i,1],20) for i in range((nb_simul*(steps+1)))]


In [27]:
dataset

S  ttm     delta
0        1.000000   20  0.000000
1        1.068078   19  0.701702
2        1.077003   18  0.707164
3        1.186345   17  0.799459
4        1.207693   16  0.808336
...           ...  ...       ...
2099995  1.101366    4  0.821394
2099996  1.129969    3  0.834673
2099997  1.196291    2  0.855370
2099998  1.273126    1  0.874675
2099999  1.231296    0  0.870140

[2100000 rows x 3 columns]

In [28]:
import numpy as np

def generate_paths(num_paths, num_steps, T, S0, r, sigma, random_seed=None):
    """
    Generates sample paths for a Geometric Brownian Motion using NumPy.
    
    Args:
        num_paths   : int, number of simulated paths
        num_steps   : int, number of time steps
        T           : float, total time horizon (e.g., 1.0 for 1 year)
        S0          : float, initial asset price
        r           : float, risk-free interest rate
        sigma       : float, volatility
        random_seed : int or None, for reproducibility of random draws

    Returns:
        A NumPy array of shape (num_paths, num_steps+1) containing the simulated paths.
    """
    if random_seed is not None:
        np.random.seed(random_seed)

    dt = T / num_steps
    # Initialize paths array
    paths = np.zeros((num_paths, num_steps + 1))
    # Set the initial value
    paths[:, 0] = S0

    for step in range(num_steps):
        Z = np.random.normal(0.0, 1.0, size=num_paths)
        # Euler-Maruyama (log form) update
        paths[:, step+1] = paths[:, step] * np.exp(
            (r - 0.5 * sigma**2) * dt + sigma * np.sqrt(dt) * Z
        )

    return paths


In [29]:
import math
from scipy.stats import norm

def bs_call_delta(moneyness, T, r, sigma):
    """
    Computes the Black-Scholes delta for a call option given moneyness = K/S.
    
    Args:
        moneyness (float or np.array): K/S
        T        (float or np.array): time to maturity
        r        : float, risk-free rate
        sigma    : float, volatility

    Returns:
        A NumPy array (or float) of the delta values.
    """
    M = np.array(moneyness, ndmin=1)  # ensure array
    time_ = np.array(T, ndmin=1)

    # To avoid dividing by zero if T=0, add a small epsilon
    epsilon = 1e-12
    time_ = np.maximum(time_, epsilon)

    # d1 = [-ln(M) + (r + 0.5*sigma^2)*T] / [sigma * sqrt(T)]
    d1 = (-np.log(M) + (r + 0.5 * sigma**2) * time_) / (sigma * np.sqrt(time_))
    
    # Standard normal CDF using the error function
    # Phi(x) = 0.5 * [1 + erf(x / sqrt(2))]
    def phi(x):
        return norm.cdf(x)
    
    delta = phi(d1)
    print(delta)
    # If inputs were scalars, return scalar
    if np.isscalar(moneyness) and np.isscalar(T):
        return delta[0]
    return delta


In [30]:

paths = generate_paths(
    num_paths=5,
    num_steps=5,
    T=1.0,
    S0=100.0,
    r=0.05,
    sigma=0.2,
    random_seed=42
)
print("Sample GBM Paths:\n", paths)

# 2) Compute delta for a single moneyness/time
single_delta = bs_call_delta(moneyness=0.95, T=0.5, r=0.05, sigma=0.2)
print("\nDelta for moneyness=0.95, T=0.5:", single_delta)

# 3) Plot the 3D surface of the delta
plot_delta_surface(r=0.05, sigma=0.2, moneyness_min=0.8, moneyness_max=1.2)


Sample GBM Paths:
 [[100.         105.17205735 103.61227469 100.00362805  95.67087736
  109.728107  ]
 [100.          99.36534897 115.12891945 111.09619012 102.08502396
  100.64625951]
 [100.         106.60188665 114.86329233 118.08260505 122.17953462
  123.65945594]
 [100.         115.28347758 111.20808122  94.28047012  87.44918853
   77.44938067]
 [100.          98.51677827 104.03786475  89.70025177  79.53150979
   76.20767821]]
[0.72913061]

Delta for moneyness=0.95, T=0.5: 0.7291306113288041


NameError: name 'plot_delta_surface' is not defined

In [43]:
# Coding of the loss function which is the Expected shortfall 
x=  np.random.randn(100000)
fig = px.histogram(x,nbins=100)

fig.show()

In [55]:
alpha = 0.05
VaR = np.quantile(x,q=alpha)

ES_alpha = np.mean(x[np.where(x<VaR)])

In [54]:
x[np.where(x<VaR)]

array([-2.28577724, -1.72601062, -2.08074053, ..., -1.7799463 ,
       -2.23498135, -1.79423564])

In [58]:
df = px.data.tips()
df

total_bill   tip     sex smoker   day    time  size
0         16.99  1.01  Female     No   Sun  Dinner     2
1         10.34  1.66    Male     No   Sun  Dinner     3
2         21.01  3.50    Male     No   Sun  Dinner     3
3         23.68  3.31    Male     No   Sun  Dinner     2
4         24.59  3.61  Female     No   Sun  Dinner     4
..          ...   ...     ...    ...   ...     ...   ...
239       29.03  5.92    Male     No   Sat  Dinner     3
240       27.18  2.00  Female    Yes   Sat  Dinner     2
241       22.67  2.00    Male    Yes   Sat  Dinner     2
242       17.82  1.75    Male     No   Sat  Dinner     2
243       18.78  3.00  Female     No  Thur  Dinner     2

[244 rows x 7 columns]